**DISCLAIMER**

By accessing this code, you acknowledge the code is made available for presentation and demonstration purposes only and that the code (1) is not subject to SOC 1 and SOC 2 compliance audits, and (2) is not designed or intended to be a substitute for the professional advice, diagnosis, treatment, or judgment of a certified financial services professional. Do not use this code to replace, substitute, or provide professional financial advice, or judgement. You are solely responsible for ensuring the regulatory, legal, and/or contractual compliance of any use of the code, including obtaining any authorizations or consents, and any solution you choose to build that incorporates this code in whole or in part.

<img src=https://brysmiwasb.blob.core.windows.net/demos/geoscan/databricks_fsi_white.png width="600px">

# Geospatial fraud detection

*A large scale fraud prevention system is usually a complex ecosystem made of various controls (all with critical SLAs), a mix of traditional rules and AI and a patchwork of technologies between proprietary on-premises systems and open source cloud technologies. In a previous [solution accelerator](https://databricks.com/blog/2021/01/19/combining-rules-based-and-ai-models-to-combat-financial-fraud.html), we addressed the problem of blending rules with AI in a common orchestration layer powered by MLFlow. In this series of notebooks centered around geospatial analytics, we demonstrate how Lakehouse enables organizations to better understand customers behaviours, no longer based on who they are, but how they bank, no longer using a one-size-fits-all rule but a truly personalized AI. After all, identifying abnormal patterns can only be made possible if one first understands what a normal behaviour is, and doing so for millions of customers becomes a challenge that requires both data and AI combined into one platform. As part of this solution, we are releasing a new open source geospatial library, [GEOSCAN](https://github.com/databrickslabs/geoscan), to detect geospatial behaviours at massive scale, track customers patterns over time and detect anomalous card transactions*

---
+ <a href="https://databricks.com/notebooks/geoscan/00_geofraud_context.html">STAGE0</a>: Home page
+ <a href="https://databricks.com/notebooks/geoscan/01_geofraud_clustering.html">STAGE1</a>: Using a novel approach to geospatial clustering with H3
+ <a href="https://databricks.com/notebooks/geoscan/02_geofraud_fraud.html">STAGE2</a>: Detecting anomalous transactions as ML enriched rules
---
<antoine.amend@databricks.com>

## Density based spatial clustering
[DBSCAN](https://www.aaai.org/Papers/KDD/1996/KDD96-037.pdf) (density-based spatial clustering of applications with noise) 
is a common clustering technique used to group points that are closely packed together. Compared to other clustering methodologies, 
it doesn't require you to indicate the number of clusters beforehand, can detect clusters of varying shapes and sizes 
and is strong at finding outliers that don't belong to any dense area, hence a great candidate for geospatial analysis of credit card 
transactions and fraud detection. This, however, comes with a serious price tag: DBSCAN requires all points to be compared 
to every other points in order to find dense neighborhoods where at least `minPts` points can be found within a `epsilon` radius. Here comes **GEOSCAN**, our novel approach to geospatial clustering.

<img src="https://upload.wikimedia.org/wikipedia/commons/thumb/0/05/DBSCAN-density-data.svg/220px-DBSCAN-density-data.svg.png">

[Source](https://en.wikipedia.org/wiki/DBSCAN)

## Introducing GEOSCAN

As we could not find any viable solution that could scale to the millions of customers or to more than a few hundreds of thousands of records, we created our own open source library, [GEOSCAN](https://github.com/databrickslabs/geoscan), our implementation of DBSCAN algorithm for geospatial clustering at big data scale. Leveraging uber [H3](https://eng.uber.com/h3/) library to only group points we know are in close vicinity (according to H3 `precision`) and relying on [GraphX](https://spark.apache.org/docs/latest/graphx-programming-guide.html) API, this framework can detect dense areas at massive scale, understanding user shopping behaviours and detecting anomalous transactions in near real time. We will be using `folium` library to visualize our approach step by step as we move from a one size fits all model to a personalized clustering and anomaly detection. 

### Step1: Grouping

The first step of GEOSCAN is to link each point to all its neighbours within an `epsilon` distance and remove points having less than `minPts` neighbours. Concretely, this means running a cartesian product - `O(n^2)` time complexity - of our dataset to filter out tuples that are more than `epsilon` meters away from one another. In our approach, we leverage H3 hexagons to only group points we know are close enough to be worth comparing. As reported in below picture, we first map a point to an H3 polygon and draw a circle of radius `epsilon` that we tile to at least 1 complete ring. Therefore, 2 points being at a distance of `epsilon` away would be sharing at least 1 polygon in common, so grouping by polygon would group points in close vicinity, ignoring 99.99% of the dataset. These pairs can then be further measured using a [haversine](https://en.wikipedia.org/wiki/Haversine_formula) distance.

<img src="https://brysmiwasb.blob.core.windows.net/demos/geoscan/geoscan_algorithm.png" width=800>

Even though the theoretical time complexity remains the same - `O(n^2)` - we did not have to run an expensive (and non realistic) cartesian product of our entire dataframe. The real time complexity is `O(p.k^2)` where `p` groups are processed in parallel, running cartesian product of `k` points (`k << n`) sharing a same H3 hexagon, hence scaling massively. This isn't magic though, and prone to failure when data is heavily skewed in dense area (we recommend sampling data in specific areas as reported later). 
 
### Step2: Clustering

The second step is trivial when using a graph paradigm. As we found vertices being no more than `epsilon` meters away (edge contains distance), we simply remove vertices with less than `minPts` connections (`degrees < minPts`). By removing these border nodes, clusters start to form and can be retrieved via a `connectedComponents`. 

### Step3: Convex Hulls

As all our core points are defining our clusters, the final step is to find the [Convex Hull](https://en.wikipedia.org/wiki/Convex_hull), that is the smallest shape that include all of our core geo coordinates. There are plenty of litterature on that topic, and our approach can easily be used in memory for each cluster returned by our connected components.

### Dependencies

In addition to GEOSCAN jar file that must be installed on classpath, we also need to install its python wrapper. Installed in the future via a pypi repo, one needs to install local files whilst our code is not yet published.

In [0]:
%pip install geojson

Python interpreter will be restarted.
Collecting geojson
 Downloading geojson-2.5.0-py2.py3-none-any.whl (14 kB)
Installing collected packages: geojson
Successfully installed geojson-2.5.0
Python interpreter will be restarted.

In [0]:
display(dbutils.fs.ls('/FileStore/demo-fsi/geoscan/python/'))

path name size dbfs:/FileStore/demo-fsi/geoscan/python/__init__.py __init__.py 0 dbfs:/FileStore/demo-fsi/geoscan/python/geoscan/ geoscan/ 0 dbfs:/FileStore/demo-fsi/geoscan/python/requirements.txt requirements.txt 41 dbfs:/FileStore/demo-fsi/geoscan/python/setup.py setup.py 616

In [0]:
%pip install /dbfs/FileStore/demo-fsi/geoscan/python folium==0.12.1 h3==3.7.1 mlflow

Python interpreter will be restarted.
Processing /dbfs/FileStore/demo-fsi/geoscan/python
 DEPRECATION: A future pip version will change local packages to be built in-place without first copying to a temporary directory. We recommend you use --use-feature=in-tree-build to test your packages with this new behavior before it becomes the default.
 pip 21.3 will remove support for this functionality. You can find discussion regarding this at https://github.com/pypa/pip/issues/7555.
Requirement already satisfied: folium==0.12.1 in /databricks/python3/lib/python3.7/site-packages (0.12.1)
Collecting h3==3.7.1
 Downloading h3-3.7.1-cp37-cp37m-manylinux2010_x86_64.whl (791 kB)
Collecting mlflow
 Using cached mlflow-1.18.0-py3-none-any.whl (14.2 MB)
Requirement already satisfied: numpy in /databricks/python3/lib/python3.7/site-packages (from folium==0.12.1) (1.18.1)
Requirement already satisfied: jinja2>=2.9 in /databricks/python3/lib/python3.7/site-packages (from folium==0.12.1) (3.0.1)
Requirement already satisfied: requests in /databricks/python3/lib/python3.7/site-packages (from folium==0.12.1) (2.22.0)
Requirement already satisfied: branca>=0.3.0 in /databricks/python3/lib/python3.7/site-packages (from folium==0.12.1) (0.4.2)
Requirement already satisfied: MarkupSafe>=2.0 in /databricks/python3/lib/python3.7/site-packages (from jinja2>=2.9->folium==0.12.1) (2.0.1)
Collecting docker>=4.0.0
 Using cached docker-5.0.0-py2.py3-none-any.whl (146 kB)
Collecting protobuf>=3.7.0
 Using cached protobuf-3.17.3-cp37-cp37m-manylinux_2_5_x86_64.manylinux1_x86_64.whl (1.0 MB)
Collecting alembic<=1.4.1
 Using cached alembic-1.4.1-py2.py3-none-any.whl
Collecting packaging
 Using cached packaging-21.0-py3-none-any.whl (40 kB)
Collecting click>=7.0
 Downloading click-8.0.1-py3-none-any.whl (97 kB)
Collecting querystring-parser
 Using cached querystring_parser-1.2.4-py2.py3-none-any.whl (7.9 kB)
Collecting databricks-cli>=0.8.7
 Using cached databricks_cli-0.14.3-py3-none-any.whl
Collecting gunicorn
 Using cached gunicorn-20.1.0-py3-none-any.whl (79 kB)
Collecting sqlalchemy
 Using cached SQLAlchemy-1.4.20-cp37-cp37m-manylinux_2_5_x86_64.manylinux1_x86_64.manylinux_2_17_x86_64.manylinux2014_x86_64.whl (1.5 MB)
Collecting Flask
 Using cached Flask-2.0.1-py3-none-any.whl (94 kB)
Requirement already satisfied: pandas in /databricks/python3/lib/python3.7/site-packages (from mlflow) (1.0.1)
Collecting gitpython>=2.1.0
 Using cached GitPython-3.1.18-py3-none-any.whl (170 kB)
Collecting pyyaml>=5.1
 Using cached PyYAML-5.4.1-cp37-cp37m-manylinux1_x86_64.whl (636 kB)
Collecting prometheus-flask-exporter
 Using cached prometheus_flask_exporter-0.18.2-py3-none-any.whl
Requirement already satisfied: entrypoints in /databricks/python3/lib/python3.7/site-packages (from mlflow) (0.3)
Collecting sqlparse>=0.3.1
 Using cached sqlparse-0.4.1-py3-none-any.whl (42 kB)
Requirement already satisfied: pytz in /databricks/python3/lib/python3.7/site-packages (from mlflow) (2019.3)
Collecting cloudpickle
 Using cached cloudpickle-1.6.0-py3-none-any.whl (23 kB)
Collecting Mako
 Using cached Mako-1.1.4-py2.py3-none-any.whl (75 kB)
Collecting python-editor>=0.3
 Using cached python_editor-1.0.4-py3-none-any.whl (4.9 kB)
Requirement already satisfied: python-dateutil in /databricks/python3/lib/python3.7/site-packages (from alembic<=1.4.1->mlflow) (2.8.1)
Collecting importlib-metadata
 Using cached importlib_metadata-4.6.1-py3-none-any.whl (17 kB)
Collecting tabulate>=0.7.7
 Using cached tabulate-0.8.9-py3-none-any.whl (25 kB)
Requirement already satisfied: six>=1.10.0 in /databricks/python3/lib/python3.7/site-packages (from databricks-cli>=0.8.7->mlflow) (1.14.0)
Collecting websocket-client>=0.32.0
 Using cached websocket_client-1.1.0-py2.py3-none-any.whl (68 kB)
Collecting gitdb<5,>=4.0.1
 Using cached gitdb-4.0.7-py3-none-any.whl (63 kB)
Collecting typing-extensions>=3.7.4.0
 Using cached typing_extensions-3.10.0.0-py3-none-any.whl (26 kB)
Collecting smmap<5,>=3.0.1
 Using cach

For the purpose of this exercise, we'll be storing a few datasets onto Delta lake that we can optimize for faster access.

In [0]:
%sql
CREATE DATABASE IF NOT EXISTS geospatial

## Exploring data
As consumers are becoming more and more digitally engaged, large financial service institutions often have access to GPS coordinates of every purchase made by their customers, in real time. With around 40 billions of card transactions being processed in the US every year, retail banks have a lot of data they could leverage to better understand customers's behaviors over time (for customers opting in GPS enabled apps). However, it often requires access to large amount of resources and cutting edge libraries to run expensive geospatial computations that do not "fit" well with a traditional data warehouse paradigm. In this example, we generated half a million of synthetic data points of geo coordinates for multiple users. This dataset can be generated on demand from the [GEOSCAN](https://github.com/databrickslabs/geoscan) project and uploaded as a csv onto Databricks `/FileStore`

In [0]:
from pyspark.sql import functions as F
from pyspark.sql.types import * 

schema = StructType([
    StructField('user', StringType()),
    StructField('latitude', DoubleType()),
    StructField('longitude', DoubleType()),
    StructField('amount', DoubleType()),
  ])

_ = (
  spark
    .read
    .format('csv')
    .option('header', 'true')
    .schema(schema)
    .load('/FileStore/tables/nyc_shapes.csv')
    .write
    .format('delta')
    .mode('overwrite')
    .saveAsTable('geospatial.transactions')
)

Our simplistic dataset only contains a tokenized value for users, a geospatial coordinate (as `latitude` and `longitude`) and a transaction `amount`. In real life, the same should also contains transaction description, timestamp, and often has been enriched with merchant and brand information (will be part of a future solution accelerator). With our data stored on a Delta table, we can optimize read access to specific fields like `user` as well as rebalancing possible small files into well defined partitions

In [0]:
%sql
OPTIMIZE geospatial.transactions ZORDER BY (user)

path metrics null List(1, 7, List(5965481, 5965481, 5965481.0, 1, 5965481), List(417581, 1006119, 920516.0, 7, 6443615), 0, List(minCubeSize(107374182400), List(0, 0), List(7, 6443615), 0, List(7, 6443615), 1, null), 1)

In [0]:
points_df = spark.read.table('geospatial.transactions')
display(points_df)

Before running our geospatial clustering, it may be worth understanding our data better. We enrich our data with H3 polygons of different dimensions to identify potential skews in our distribution, these high street places or large retail mall "attracting" most of transactions,  acting as evident bottlenecks for large `epsilon` values. In addition to the `GeoUtils` class available on GEOSCAN package, H3 can also be used natively via a python API.

In [0]:
import h3
from pyspark.sql.functions import udf
from pyspark.sql import functions as F

@udf("string")
def to_h3(lat, lng, precision):
  h = h3.geo_to_h3(lat, lng, precision)
  return h.upper()

display(
  spark.read.table('geospatial.transactions')
    .groupBy(to_h3(F.col('latitude'), F.col('longitude'), F.lit(9)).alias('h3'))
    .count()
    .orderBy(F.desc('count'))
)

h3 count 892A100896BFFFF 3491 892A1072C07FFFF 3195 892A1072CABFFFF 2653 892A100D237FFFF 2627 892A100D24BFFFF 2612 892A100D25BFFFF 2552 892A107252FFFFF 2500 892A1072523FFFF 2464 892A1072197FFFF 2420 892A107252BFFFF 2420 892A1072C17FFFF 2338 892A107253BFFFF 2330 892A1072193FFFF 2292 892A10721B3FFFF 2287 892A1072CA7FFFF 2246 892A1072CA3FFFF 2238 892A1072DDBFFFF 2237 892A1072187FFFF 2230 892A1072CB7FFFF 2163 892A100D3CBFFFF 2122 892A1072507FFFF 2110 892A1072DD7FFFF 2099 892A10089A7FFFF 2097 892A100D24FFFFF 2078 892A100D67BFFFF 2076 892A1072CAFFFFF 2074 892A100D243FFFF 2035 892A100D6B3FFFF 2029 892A100D3DBFFFF 1988 892A10088BBFFFF 1974 892A100D4DBFFFF 1960 892A1072533FFFF 1947 892A1072DCBFFFF 1929 892A100D233FFFF 1928 892A100D253FFFF 1921 892A100AA33FFFF 1918 892A1072DC3FFFF 1873 892A100888FFFFF 1858 892A100893BFFFF 1806 892A1072DD3FFFF 1796 892A1072C37FFFF 1780 892A1072CBBFFFF 1777 892A100D21BFFFF 1775 892A100D2AFFFFF 1767 892A100D2CFFFFF 1718 892A100D623FFFF 1697 892A1008887FFFF 1684 892A1072C33FFFF 1660 892A1072D9BFFFF 1654 892A100892BFFFF 1619 892A100D203FFFF 1617 892A100D6BBFFFF 1575 892A1072C0FFFFF 1562 892A100D227FFFF 1555 892A100888BFFFF 1546 892A100D60BFFFF 1545 892A100D37BFFFF 1528 892A100D257FFFF 1515 892A1008883FFFF 1508 892A100D36BFFFF 1484 892A10725ABFFFF 1480 892A100D647FFFF 1455 892A100D673FFFF 1390 892A100D63BFFFF 1348 892A100D3CFFFFF 1344 892A1072527FFFF 1315 892A100D66BFFFF 1314 892A1008987FFFF 1282 892A100D633FFFF 1278 892A100D3C3FFFF 1269 892A1072C3BFFFF 1267 892A100D213FFFF 1262 892A100D223FFFF 1252 892A100D657FFFF 1243 892A100D617FFFF 1188 892A100D45BFFFF 1187 892A1072C27FFFF 1183 892A100AA23FFFF 1165 892A100D44BFFFF 1127 892A1072CB3FFFF 1113 892A1008833FFFF 1112 892A1072D53FFFF 1109 892A100D2ABFFFF 1098 892A100D207FFFF 1098 892A1008927FFFF 1040 892A100D293FFFF 1028 892A1072183FFFF 1019 892A100D603FFFF 1013 892A10725B7FFFF 1011 892A100D14FFFFF 1009 892A100D663FFFF 1008 892A100AA2FFFFF 1002 892A1008823FFFF 999 892A100D62FFFFF 999 892A1072D33FFFF 996 892A100D61BFFFF 994 892A100D287FFFF 994 892A100D62BFFFF 976 892A100D64FFFFF 963 892A10725AFFFFF 963 892A100D6ABFFFF 963 892A100D36FFFFF 960 892A100D6AFFFFF 956 892A100D2C7FFFF 956 892A100882FFFFF 929 892A100D65BFFFF 928 892A100D643FFFF 917 892A1008983FFFF 916 892A100D0B3FFFF 915 892A1008C93FFFF 903 892A1072577FFFF 883 892A100D247FFFF 877 892A1072D3BFFFF 876 892A1008923FFFF 869 892A100D68FFFFF 857 892A100882BFFFF 857 892A100D54BFFFF 850 892A10721B7FFFF 847 892A1008B87FFFF 845 892A1072597FFFF 844 892A1072DCFFFFF 843 892A100D627FFFF 839 892A100D263FFFF 837 892A100F277FFFF 837 892A1072D23FFFF 835 892A1008C97FFFF 834 892A100D687FFFF 832 892A100D363FFFF 826 892A1072C8FFFFF 825 892A100898FFFFF 817 892A100D667FFFF 810 892A1008BBBFFFF 807 892A100D26BFFFF 802 892A1072593FFFF 801 892A100D26FFFFF 799 892A100D64BFFFF 795 892A100D087FFFF 793 892A1072583FFFF 792 892A1008B97FFFF 791 892A1072CD3FFFF 790 892A1008B2FFFFF 789 892A100D677FFFF 785 892A1008977FFFF 783 892A107250FFFFF 780 892A100D613FFFF 775 892A10088AFFFFF 773 892A100F23BFFFF 770 892A100D693FFFF 766 892A1072D07FFFF 756 892A1008933FFFF 755 892A100D2C3FFFF 754 892A1072587FFFF 751 892A1072CC7FFFF 750 892A1008837FFFF 750 892A100AB4FFFFF 749 892A100D143FFFF 742 892A100D54FFFFF 737 892A100F22BFFFF 734 892A100D217FFFF 734 892A100D697FFFF 732 892A100D637FFFF 730 892A1008997FFFF 725 892A100D6A3FFFF 723 892A10089B3FFFF 720 892A100AB43FFFF 718 892A100D373FFFF 716 892A100AB5BFFFF 715 892A100D147FFFF 712 892A100D23BFFFF 702 892A10089BBFFFF 692 892A1008B27FFFF 689 892A100890FFFFF 685 892A1072C8BFFFF 679 892A100D443FFFF 671 892A10721BBFFFF 656 892A100D28FFFFF 650 892A1008827FFFF 649 892A100D283FFFF 648 892A1072817FFFF 645 892A100D28BFFFF 644 892A1072CD7FFFF 641 892A1072C13FFFF 638 892A100AB4BFFFF 637 892A1008993FFFF 636 892A100D2CBFFFF 636 892A1072C03FFFF 634 892A1072D0FFFFF 622 892A107288FFFFF 622 892A1008937FFFF 618 892A1072887FFFF 617 892A100D22FFFFF 615 892A1072CC3FFFF 613 892A100D653FFFF 606 892A1072C9BFFFF 605 892A100F223FFFF 598

At resolution 9 (the resolution table can be found [here](https://h3geo.org/docs/core-library/restable)), or approximately 150m radius, we observe a few areas with about 3,000 observations. At such a granularity, our model would still need to compute 3,000 x 3,000 pairwise distances. Although this is by far better than 500,000 x 500,000 that would be required with a traditional DBSCAN approach, we show later how to sample our dataset geographically to remove possible skews whilst maintaining GEOSCAN predictive power.

It is always a a good practice to randomly sample a few data points to visualize them directly on a map and identify possible densed area. In below visualization, we use `folium` to render 1% of our observations as a heatmap.

In [0]:
import folium
from folium import plugins

points = spark.read.table('geospatial.transactions').sample(0.1).toPandas()[['latitude', 'longitude']]
nyc = folium.Map([40.75466940037548,-73.98365020751953], zoom_start=12, width='80%', height='100%')
folium.TileLayer('Stamen Toner').add_to(nyc)
nyc.add_child(plugins.HeatMap(points.to_numpy(), radius=12))
nyc

Out[4]:

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe src="about:blank" style="position:absolute;width:100%;height:100%;left:0;top:0;border:none !important;" data-html=%3C%21DOCTYPE%20html%3E%0A%3Chead%3E%20%20%20%20%0A%20%20%20%20%3Cmeta%20http-equiv%3D%22content-type%22%20content%3D%22text/html%3B%20charset%3DUTF-8%22%20/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%3Cscript%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20L_NO_TOUCH%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20L_DISABLE_3D%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%3C/script%3E%0A%20%20%20%20%0A%20%20%20%20%3Cstyle%3Ehtml%2C%20body%20%7Bwidth%3A%20100%25%3Bheight%3A%20100%25%3Bmargin%3A%200%3Bpadding%3A%200%3B%7D%3C/style%3E%0A%20%20%20%20%3Cstyle%3E%23map%20%7Bposition%3Aabsolute%3Btop%3A0%3Bbottom%3A0%3Bright%3A0%3Bleft%3A0%3B%7D%3C/style%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//code.jquery.com/jquery-1.12.4.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/js/bootstrap.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js%22%3E%3C/script%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css%22/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cmeta%20name%3D%22viewport%22%20content%3D%22width%3Ddevice-width%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20initial-scale%3D1.0%2C%20maximum-scale%3D1.0%2C%20user-scalable%3Dno%22%20/%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cstyle%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%23map_47b49a88472d48c99efbb25450d51753%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20position%3A%20relative%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20width%3A%2080.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20height%3A%20100.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20left%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20top%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7D%0A%20%20%20%20%20%20%20%20%20%20%20%20%3C/style%3E%0A%20%20%20%20%20%20%20%20%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium%40master/folium/templates/leaflet_heat.min.js%22%3E%3C/script%3E%0A%3C/head%3E%0A%3Cbody%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cdiv%20class%3D%22folium-map%22%20id%3D%22map_47b49a88472d48c99efbb25450d51753%22%20%3E%3C/div%3E%0A%20%20%20%20%20%20%20%20%0A%3C/body%3E%0A%3Cscript%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20var%20map_47b49a88472d48c99efbb25450d51753%20%3D%20L.map%28%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%22map_47b49a88472d48c99efbb25450d51753%22%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20center%3A%20%5B40.75466940037548%2C%20-73.98365020751953%5D%2C%0A%20%20%2

In [0]:
#Chart for all transactions in NYC
#Convert points to csv for PowerBI
points.to_csv('/dbfs/FileStore/nyc_points.csv', index=False)

![folium](https://brysmiwasb.blob.core.windows.net/demos/geoscan/geoscan_folium_1.png)

Our synthetic data set exhibits denser areas around Chelsea, East village and the financial district. By zooming in, we can reveal well defined zones that we aim at programmatically extracting using GEOSCAN

## Distributed clustering
Working **fully distributed**, we retrieve clusters from an entire dataframe (i.e. across all our users) using the Spark ML API, hence fully compliant with the Spark Pipeline framework (model can be serialized / deserialized). In this mode, the core of GEOSCAN algorithm relies on GraphX to detect points having `distance < epsilon` and a `degree > minPoints`. Before running our model full scale it is always good practice to run it on a smaller sample first. We'll be using only ~ 20,000 records at first (5% of population).

In [0]:
points_sampled = points_df.sample(0.05)

### Model training

We will be using a relatively small `epsilon` value at first to overcome the skews observed earlier. Furthermore, given the amount of data we have in dense areas, having `minPts` too low would result in the entire shape of NYC to be returned as one cluster. How do we tune `epsilon`? Largely domain-specific and with no established strategy, a rule of thumb could be to plot k nearest neighbors, looking at distances and choosing the point of max curvature (more [information](https://towardsdatascience.com/machine-learning-clustering-dbscan-determine-the-optimal-value-for-epsilon-eps-python-example-3100091cfbc)). We leave this to the discretion of the reader. We will try different approaches with different values of `epsilon` and `minPts`, using folium to visualize and refine our clustering strategy

In [0]:
from geoscan import Geoscan
import mlflow

with mlflow.start_run(run_name='GEOSCAN') as run:

  geoscan = Geoscan() \
    .setLatitudeCol('latitude') \
    .setLongitudeCol('longitude') \
    .setPredictionCol('cluster') \
    .setEpsilon(200) \
    .setMinPts(20)
   
  mlflow.log_param('epsilon', 200)
  mlflow.log_param('minPts', 20)
  
  model = geoscan.fit(points_sampled)
  mlflow.spark.log_model(model, "geoscan")
  run_id = run.info.run_id

Using these parameters, we've extracted 14 distinct areas on 20k records in about a mn. As strong advocate of open standard, we build GEOSCAN to support GeoJSON [rfc7946](https://tools.ietf.org/html/rfc7946) as model output. For convenience, we can attach GeoJson file as an artifact alongside the model on mlflow (file will be visualized as-is on mlflow tracking server).

In [0]:
geoJson = model.toGeoJson()
with open('/tmp/geoscan.geojson', 'w') as f:
  f.write(geoJson)

import mlflow
client = mlflow.tracking.MlflowClient()
client.log_artifact(run_id, "/tmp/geoscan.geojson")

With our model exported as GeoJson object, we can overlay our clusters on a same `folium` visualization.

In [0]:
folium.GeoJson(geoJson).add_to(nyc)
nyc

Out[9]:

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe src="about:blank" style="position:absolute;width:100%;height:100%;left:0;top:0;border:none !important;" data-html=%3C%21DOCTYPE%20html%3E%0A%3Chead%3E%20%20%20%20%0A%20%20%20%20%3Cmeta%20http-equiv%3D%22content-type%22%20content%3D%22text/html%3B%20charset%3DUTF-8%22%20/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%3Cscript%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20L_NO_TOUCH%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20L_DISABLE_3D%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%3C/script%3E%0A%20%20%20%20%0A%20%20%20%20%3Cstyle%3Ehtml%2C%20body%20%7Bwidth%3A%20100%25%3Bheight%3A%20100%25%3Bmargin%3A%200%3Bpadding%3A%200%3B%7D%3C/style%3E%0A%20%20%20%20%3Cstyle%3E%23map%20%7Bposition%3Aabsolute%3Btop%3A0%3Bbottom%3A0%3Bright%3A0%3Bleft%3A0%3B%7D%3C/style%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//code.jquery.com/jquery-1.12.4.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/js/bootstrap.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js%22%3E%3C/script%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css%22/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cmeta%20name%3D%22viewport%22%20content%3D%22width%3Ddevice-width%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20initial-scale%3D1.0%2C%20maximum-scale%3D1.0%2C%20user-scalable%3Dno%22%20/%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cstyle%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%23map_47b49a88472d48c99efbb25450d51753%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20position%3A%20relative%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20width%3A%2080.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20height%3A%20100.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20left%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20top%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7D%0A%20%20%20%20%20%20%20%20%20%20%20%20%3C/style%3E%0A%20%20%20%20%20%20%20%20%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium%40master/folium/templates/leaflet_heat.min.js%22%3E%3C/script%3E%0A%3C/head%3E%0A%3Cbody%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cdiv%20class%3D%22folium-map%22%20id%3D%22map_47b49a88472d48c99efbb25450d51753%22%20%3E%3C/div%3E%0A%20%20%20%20%20%20%20%20%0A%3C/body%3E%0A%3Cscript%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20var%20map_47b49a88472d48c99efbb25450d51753%20%3D%20L.map%28%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%22map_47b49a88472d48c99efbb25450d51753%22%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20center%3A%20%5B40.75466940037548%2C%20-73.98365020751953%5D%2C%0A%20%20%2

One can play with different `epsilon` and `minPts` values resulting in clusters of different sizes and shapes. As discussed, tuning geospatial clustering model mainly relies on domain expertise than golden standard rule. As represented above, our parameters resulted in a relative large shape covering most of Manhattan. Although reducing `minPts` value could help refining that shape, it may certainly impact less dense areas such as Williamsburg. In addition to performance gain, sampling our data may become handy if not necessary.

### Performance tuning
Given the skews observed in our data distribution, it is expected to take more time for algoritm to group points to their nearest neighborood with large `epsilon` values. Although we clearly beat the `O(N^2)` curse of DBSCAN with well distributed data, training on skewed dataset tend to same time complexity (minus the technical limits imposed by memory) as `n` points would share same polygons `P x O(n^2) = O(n^2)`. Using simple UDF and native H3 library, one could reduce the complexity by sampling transactions to maximum of X points within a same radius (we will be using a sampling resolution of 11)

In [0]:
import random
from pyspark.sql.types import *

# we randomly select maximum 10 points within a same polygon of size 11 (30m)
def sample(latitudes, longitudes):
  l = list(zip(latitudes, longitudes))
  return random.sample(l, min(len(l), 10))

sample_schema = ArrayType(StructType([StructField("latitude", DoubleType()), StructField("longitude", DoubleType())]))
sample_udf = udf(sample, sample_schema)

sample_df = (
  points_df
    .groupBy(to_h3(F.col("latitude"), F.col("longitude"), F.lit(11)))
    .agg(F.collect_list(F.col("latitude")).alias("latitudes"), F.collect_list(F.col("longitude")).alias("longitudes"))
    .withColumn('sample', F.explode(sample_udf(F.col('latitudes'), F.col('longitudes'))))
    .select('sample.latitude', 'sample.longitude')
)

display(
  sample_df
    .groupBy(to_h3(F.col("latitude"), F.col("longitude"), F.lit(9)).alias("h3"))
    .count()
    .orderBy(F.desc("count"))
)

h3 count 892A100D0B3FFFF 507 892A1072507FFFF 506 892A1072DC3FFFF 501 892A100AA2FFFFF 501 892A100882FFFFF 501 892A100D3DBFFFF 500 892A100D24BFFFF 499 892A100D677FFFF 499 892A100893BFFFF 498 892A107252BFFFF 497 892A100D647FFFF 497 892A1008B2FFFFF 496 892A1072CA3FFFF 496 892A100D233FFFF 496 892A100D213FFFF 496 892A100D6BBFFFF 496 892A107252FFFFF 496 892A1072C17FFFF 496 892A1072CB7FFFF 495 892A1072193FFFF 494 892A100F277FFFF 494 892A100D54BFFFF 494 892A1072C07FFFF 493 892A1072197FFFF 493 892A1072DD3FFFF 493 892A100D26FFFFF 493 892A1072583FFFF 492 892A100D243FFFF 492 892A100D6B3FFFF 492 892A100D25BFFFF 492 892A100D14FFFFF 491 892A100D36BFFFF 491 892A1072187FFFF 491 892A1072597FFFF 491 892A1008B87FFFF 491 892A1072DDBFFFF 490 892A10721B3FFFF 490 892A1072593FFFF 489 892A100D67BFFFF 489 892A1008833FFFF 488 892A100D44BFFFF 488 892A100D287FFFF 488 892A100D293FFFF 488 892A1072C37FFFF 488 892A1008927FFFF 488 892A100D223FFFF 487 892A1008823FFFF 487 892A100D237FFFF 487 892A1008987FFFF 487 892A100D623FFFF 486 892A100D26BFFFF 486 892A107253BFFFF 486 892A100D2C7FFFF 486 892A100D24FFFFF 486 892A1072CABFFFF 486 892A1072CD3FFFF 486 892A1072533FFFF 486 892A10088AFFFFF 485 892A100D3CBFFFF 484 892A1072523FFFF 484 892A100D21BFFFF 484 892A100D633FFFF 484 892A100D603FFFF 484 892A100D63BFFFF 483 892A1072DCBFFFF 483 892A100D65BFFFF 483 892A1072CBBFFFF 483 892A100D2CFFFFF 483 892A100D207FFFF 482 892A1072C0FFFFF 482 892A1072DD7FFFF 481 892A100D227FFFF 480 892A100D61BFFFF 480 892A10725B7FFFF 480 892A100AB4FFFFF 480 892A100D62BFFFF 479 892A1072CA7FFFF 479 892A100D203FFFF 478 892A1072887FFFF 477 892A1072CAFFFFF 477 892A1072D07FFFF 476 892A1008BBBFFFF 476 892A107288FFFFF 476 892A100D663FFFF 476 892A100D60BFFFF 476 892A100D657FFFF 475 892A1072CC3FFFF 475 892A1072CC7FFFF 474 892A100D3CFFFFF 474 892A10088BBFFFF 474 892A1072817FFFF 474 892A100D253FFFF 472 892A100D263FFFF 471 892A1072D3BFFFF 471 892A100D36FFFFF 471 892A100F23BFFFF 470 892A100D54FFFFF 470 892A1072D23FFFF 469 892A100D62FFFFF 468 892A1008D9BFFFF 467 892A100D357FFFF 467 892A100882BFFFF 467 892A100D28FFFFF 463 892A100892BFFFF 463 892A100D30BFFFF 463 892A100D2ABFFFF 462 892A1072CD7FFFF 462 892A100D6AFFFFF 461 892A100D45BFFFF 460 892A1072D9BFFFF 459 892A1072587FFFF 458 892A100D087FFFF 457 892A1072D2BFFFF 457 892A100D66BFFFF 456 892A1008DABFFFF 456 892A100AB43FFFF 456 892A100D363FFFF 455 892A100D673FFFF 454 892A100D2BBFFFF 454 892A10725ABFFFF 453 892A100D257FFFF 452 892A100D283FFFF 451 892A1008B97FFFF 451 892A100D64BFFFF 451 892A100D667FFFF 451 892A100D617FFFF 451 892A100D217FFFF 450 892A1072C9BFFFF 448 892A1072C13FFFF 448 892A100D157FFFF 448 892A100D22FFFFF 448 892A1008C93FFFF 447 892A100D2AFFFFF 447 892A1072D33FFFF 446 892A100F22BFFFF 445 892A100D147FFFF 445 892A100D297FFFF 445 892A1008D13FFFF 444 892A1072527FFFF 443 892A1008C8FFFFF 442 892A1072897FFFF 441 892A1008D8BFFFF 441 892A1072D67FFFF 439 892A100D2C3FFFF 439 892A100D273FFFF 438 892A100D607FFFF 438 892A100D143FFFF 438 892A1072C8BFFFF 438 892A1008993FFFF 436 892A1072993FFFF 435 892A100D613FFFF 434 892A1008997FFFF 434 892A100D373FFFF 434 892A100D27BFFFF 432 892A1008CABFFFF 430 892A1072D2FFFFF 430 892A1008923FFFF 430 892A1008DA3FFFF 430 892A100D64FFFFF 428 892A100D6ABFFFF 428 892A10725AFFFFF 427 892A100888FFFFF 426 892A100D643FFFF 426 892A100D247FFFF 426 892A1008C17FFFF 425 892A1008B27FFFF 423 892A1008983FFFF 421 892A1072CB3FFFF 420 892A100D653FFFF 420 892A100D31BFFFF 419 892A100898FFFFF 418 892A1008DD7FFFF 417 892A100D2CBFFFF 415 892A100D11BFFFF 412 892A1072C8FFFFF 411 892A1072D0FFFFF 408 892A100D637FFFF 408 892A100AB5BFFFF 408 892A1072C33FFFF 408 892A100AB4BFFFF 407 892A1008C97FFFF 406 892A10089BBFFFF 406 892A100D28BFFFF 405 892A100D10BFFFF 402 892A100D543FFFF 401 892A1072C97FFFF 397 892A1008B83FFFF 397 892A10721B7FFFF 397 892A1008887FFFF 396 892A107258FFFFF 395 892A100D37BFFFF 395 892A100D377FFFF 395 892A100D1CFFFFF 393 892A100D627FFFF 393 892A1072537FFFF 392 892A1072CCFFFFF 391 892A100D2D7FFFF 391 892A1008837FFFF 389 892A10728BBFFFF 388 892A100D35B

By taking at most 10 random point in each polygon of size 30m, we drastically dropped our skew by 80%, resulting in a much more even distribution of our data. Still, with at most 10 points per 30m, we still satisfy our GEOSCAN criteria (`10 > minPts` and `30 < epsilon`). This, of course, is a simple example and would require further understanding on the data distribution and a possible dynamic sampling strategy for different areas.

### Model inference

As the core of GEOSCAN logic relies on the use of H3 polygons, it becomes natural to leverage the same for model inference instead of bringing in extra GIS dependencies for expensive [point in polygons](https://en.wikipedia.org/wiki/Point_in_polygon) queries. Our approach consists in "tiling" our clusters with H3 hexagons that can easily be joined to our original dataframe. The logic is abstracted through the `transform` method of our `Estimator` Spark interface.

In [0]:
from pyspark.sql import functions as F

display(
  model
    .transform(points_df)
    .groupBy('cluster')
    .count()
    .orderBy(F.asc('cluster'))
)

cluster count null 47848 0 213709 1 20951 2 6128 3 6598 4 6152 5 6173 6 5565 7 4623 8 2970 9 4055 10 2938 11 1914 12 3361 13 3488

We do not seem to get much more insights using a one size-fits-all clustering strategy across our entire customer base as most of transactions happens in NYC central. However, we could wonder where could we find our 32,000 "non clustered" transactions. Could we consider those as possible anomalous transactions?

In [0]:
from folium.plugins import MarkerCluster

nyc_anomalies_points = model.transform(points_df).filter(F.expr('cluster IS NULL')).sample(0.01).toPandas()
nyc_anomalies = folium.Map([40.75466940037548,-73.98365020751953], zoom_start=12, width='80%', height='100%')
folium.TileLayer('Stamen Toner').add_to(nyc_anomalies)
folium.GeoJson(geoJson, name="geojson").add_to(nyc_anomalies)
for _, point in nyc_anomalies_points.iterrows():
  folium.CircleMarker([point.latitude, point.longitude], radius=2, color='red').add_to(nyc_anomalies)

nyc_anomalies

Out[12]:

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe src="about:blank" style="position:absolute;width:100%;height:100%;left:0;top:0;border:none !important;" data-html=%3C%21DOCTYPE%20html%3E%0A%3Chead%3E%20%20%20%20%0A%20%20%20%20%3Cmeta%20http-equiv%3D%22content-type%22%20content%3D%22text/html%3B%20charset%3DUTF-8%22%20/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%3Cscript%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20L_NO_TOUCH%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20L_DISABLE_3D%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%3C/script%3E%0A%20%20%20%20%0A%20%20%20%20%3Cstyle%3Ehtml%2C%20body%20%7Bwidth%3A%20100%25%3Bheight%3A%20100%25%3Bmargin%3A%200%3Bpadding%3A%200%3B%7D%3C/style%3E%0A%20%20%20%20%3Cstyle%3E%23map%20%7Bposition%3Aabsolute%3Btop%3A0%3Bbottom%3A0%3Bright%3A0%3Bleft%3A0%3B%7D%3C/style%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//code.jquery.com/jquery-1.12.4.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/js/bootstrap.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js%22%3E%3C/script%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css%22/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cmeta%20name%3D%22viewport%22%20content%3D%22width%3Ddevice-width%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20initial-scale%3D1.0%2C%20maximum-scale%3D1.0%2C%20user-scalable%3Dno%22%20/%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cstyle%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%23map_80cd63724e534fac99ae7ac57e4ea603%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20position%3A%20relative%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20width%3A%2080.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20height%3A%20100.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20left%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20top%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7D%0A%20%20%20%20%20%20%20%20%20%20%20%20%3C/style%3E%0A%20%20%20%20%20%20%20%20%0A%3C/head%3E%0A%3Cbody%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cdiv%20class%3D%22folium-map%22%20id%3D%22map_80cd63724e534fac99ae7ac57e4ea603%22%20%3E%3C/div%3E%0A%20%20%20%20%20%20%20%20%0A%3C/body%3E%0A%3Cscript%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20var%20map_80cd63724e534fac99ae7ac57e4ea603%20%3D%20L.map%28%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%22map_80cd63724e534fac99ae7ac57e4ea603%22%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20center%3A%20%5B40.75466940037548%2C%20-73.98365020751953%5D%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20crs%3A%20L.CRS.EPSG3857%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20zoom%3A%2012%2C%0

Given that clusters are density based, it is expected to find un-clustered points located near the edges of our clusters, probably still `epsilon` meters away from their neighbours but having less than `minPts` neighbours. In order to accomodate fraud detection use cases, we may want to expand our clusters slightly to incorporate transactions at a close vicinity.

Supporting the Spark ML API, our model can be serialized / deserialized as-is, outputing data as a GeoJson file as previously discussed.

In [0]:
%fs rm -r dbfs:/FileStore/demo-fsi/models/geoscan

res0: Boolean = true

In [0]:
model.save('/FileStore/demo-fsi/models/geoscan')

In [0]:
from geoscan import GeoscanModel
model = GeoscanModel.load('/FileStore/demo-fsi/models/geoscan')

## Personalized clustering
In the previous section, we demonstrate how GEOSCAN can be used across our entire dataset. However, the aim was not to machine learn the NYC shape file, nor to find the best place to go shopping, but to track user shopping behaviour over time, where they may live, work, shop, etc. and where transactions are the least expected to happen in order to identify anomalous events. GEOSCAN supports a **pseudo distributed** approach where millions of models can be trained in parallel for millions of customers. Given that we drastically reduce the number of data to be processed for each user, we can afford to be much more targeted with higher `epsilon` values and lower `minPts`

In [0]:
from geoscan import GeoscanPersonalized
import mlflow

with mlflow.start_run(run_name='GEOSCAN_PERSONALIZED') as run:

  geoscan = GeoscanPersonalized() \
    .setLatitudeCol('latitude') \
    .setLongitudeCol('longitude') \
    .setPredictionCol('cluster') \
    .setGroupedCol('user') \
    .setEpsilon(500) \
    .setMinPts(3)

  models = geoscan.fit(points_df)
  
  mlflow.log_param('epsilon', 500)
  mlflow.log_param('minPts', 3)
  run_id = run.info.run_id

Training 200 models in parallel tooks only a couple of minutes on our entire dataset and on a small policy cluster. Note that our Spark model is no longer returning a unique model but a collection of GeoJson objects that can be accessed via a spark dataframe and stored on Delta table. Similar to our distributed approach, models can be stored and retrieved as per standard Spark API as follows. One caveat is that - instead of returning an in memory object - our model returns a dataframe that will be re-evaluated to subsequent actions. We therefore recomment persisting it / reloading first.

In [0]:
%fs rm -r dbfs:/FileStore/demo-fsi/models/geoscan_personalized

res1: Boolean = true

In [0]:
#models
models.save('/FileStore/demo-fsi/models/geoscan_personalized')

In [0]:
from geoscan import GeoscanPersonalizedModel
model_personalized = GeoscanPersonalizedModel.load('/FileStore/demo-fsi/models/geoscan_personalized')

Instead of one large GeoJson object, we access a dataframe object for each user and its respective clusters as GeoJson formatted records

In [0]:
geoJsons = model_personalized.toGeoJson()
display(geoJsons)

With all records available, one can easily select a specific slice for a given user and overlay with its respecting transactions as a heatmap

In [0]:
from pyspark.sql import functions as F

user = '8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d'
personalized_geojson = geoJsons.filter(F.col('user') == user).toPandas().iloc[0].cluster
personalized_data = points_df.filter(F.col('user') == user).toPandas()[['latitude', 'longitude']]

nyc_personalized = folium.Map([40.75466940037548,-73.98365020751953], zoom_start=12, width='80%', height='100%')
folium.TileLayer('Stamen Toner').add_to(nyc_personalized)
nyc_personalized.add_child(plugins.HeatMap(personalized_data.to_numpy(), radius=16))
folium.GeoJson(personalized_geojson, name="geojson").add_to(nyc_personalized)
nyc_personalized

Out[19]:

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe src="about:blank" style="position:absolute;width:100%;height:100%;left:0;top:0;border:none !important;" data-html=%3C%21DOCTYPE%20html%3E%0A%3Chead%3E%20%20%20%20%0A%20%20%20%20%3Cmeta%20http-equiv%3D%22content-type%22%20content%3D%22text/html%3B%20charset%3DUTF-8%22%20/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%3Cscript%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20L_NO_TOUCH%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20L_DISABLE_3D%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%3C/script%3E%0A%20%20%20%20%0A%20%20%20%20%3Cstyle%3Ehtml%2C%20body%20%7Bwidth%3A%20100%25%3Bheight%3A%20100%25%3Bmargin%3A%200%3Bpadding%3A%200%3B%7D%3C/style%3E%0A%20%20%20%20%3Cstyle%3E%23map%20%7Bposition%3Aabsolute%3Btop%3A0%3Bbottom%3A0%3Bright%3A0%3Bleft%3A0%3B%7D%3C/style%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//code.jquery.com/jquery-1.12.4.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/js/bootstrap.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js%22%3E%3C/script%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css%22/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cmeta%20name%3D%22viewport%22%20content%3D%22width%3Ddevice-width%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20initial-scale%3D1.0%2C%20maximum-scale%3D1.0%2C%20user-scalable%3Dno%22%20/%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cstyle%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%23map_7d0e0d760b434c239efbd9900a538a0d%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20position%3A%20relative%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20width%3A%2080.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20height%3A%20100.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20left%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20top%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7D%0A%20%20%20%20%20%20%20%20%20%20%20%20%3C/style%3E%0A%20%20%20%20%20%20%20%20%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium%40master/folium/templates/leaflet_heat.min.js%22%3E%3C/script%3E%0A%3C/head%3E%0A%3Cbody%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cdiv%20class%3D%22folium-map%22%20id%3D%22map_7d0e0d760b434c239efbd9900a538a0d%22%20%3E%3C/div%3E%0A%20%20%20%20%20%20%20%20%0A%3C/body%3E%0A%3Cscript%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20var%20map_7d0e0d760b434c239efbd9900a538a0d%20%3D%20L.map%28%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%22map_7d0e0d760b434c239efbd9900a538a0d%22%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20center%3A%20%5B40.75466940037548%2C%20-73.98365020751953%5D%2C%0A%20%20%2

In [0]:
#Export personalized data coordinates for a5359bd7-063d-489d-b247-c92ae389c7f2 as csv
points_df.filter(F.col('user') == user).toPandas().to_csv('/dbfs/FileStore/geospatial_fraud_detection/personalized_data_a5359bd7-063d-489d-b247-c92ae389c7f2.csv' ,index=False)

In [0]:
#Export personalized data cluster for 031e205f-7649-4ae5-95f3-aadb0642022f as geojson
import geojson
with open('/dbfs/FileStore/geospatial_fraud_detection/personalized_geojson_a5359bd7-063d-489d-b247-c92ae389c7f2.geojson', 'w') as f:
   geojson.dump(geojson.loads(personalized_geojson), f)

As reported in the above picture, we've gained further insights around a specific user's behaviour. This indicates 4 zones where this user may be the most likely to shop. Although this visualization flags what anyone could easily eye-ball, doing so programmatically was not an easy undertaking and helps us leverage the `Estimator` interface to classify all transactions for every users to their respective clusters in an easy and performant way.

In [0]:
display(model_personalized.transform(points_df))

Although a transaction happening outside of any of these clusters could not necessarily be fraudulent, such anomalous patterns would be worth flagging as a potential feature that can be combined in an overhatching [framework](https://databricks.com/blog/2021/01/19/combining-rules-based-and-ai-models-to-combat-financial-fraud.html) to combat financial fraud.

### Understanding customers patterns
Before investigating our fraud use case further, it is important to step back and reflect on the insights we have been able to gain so far. As we have been able to learn more about our entire customer base (distributed approach), we could leverage this information to better understand the behaviour that are specific to each individual. If everyone were to shop at a same location, such an area would be less specific to a particular user. We can detect "personalized" zones as how much they overlap with common areas, better understanding our customers and paving the way towards truly personalized banking.

We extended our Spark models to support a `getTiles` method that (as it says on the tin) will "fill" our polygons with H3 tiles of a given precision. Furthermore, taking into consideration our edge conditions, one can relax our boundary by allowing tiles to slightly spill over by 1,2, or X additional layers, capturing nearby transactions. Note that high H3 resolution will better fit a polygon but also requires more memory to keep all tiles, so one may have to balance between accuracy and memory constraints. Whilst you can store tiles as-is and move to next notebook, we want to explore that concept of personalized finance a bit more.

In [0]:
personalized_tiles = model_personalized.getTiles(precision=10, layers=5)
display(personalized_tiles)

user cluster h3 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2737FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D49AFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D4D77FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2317FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F229FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2AD7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2207FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F239FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F20EFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F3537FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F26A7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F262FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2017FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D4927FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F272FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2637FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2367FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F20F7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2707FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F228FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2067FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2217FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F209FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F238FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F3587FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D4937FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2717FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F22F7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F35AFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2AB7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F269FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F208FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2647FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F279FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F22A7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F3597FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F26CFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D4D67FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F20D7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F222FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F218FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2AC7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2307FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F27A7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2007FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2AEFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2617FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D4837FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F232FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F24CFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2357FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F20AFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F3D87FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D496FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2057FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2A9FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2667FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2247FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D4917FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F22DFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2327FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F3D97FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100D499FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F26EFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2AE7FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2B9FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2747FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2447FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2A8FFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2A17FFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F22CFFFF 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2257FFF 8d08c2ba-6e15-4bb0-aa6c-

We represent below our tiling methodology with additional 2 layers, stretching our Geoshape (solid line) by a couple of hundreds meters to capture nearby transactions

Detecting areas that are the most descriptive for each user is similar to detecting keywords that are more descriptive to each sentence in Natural Language processing use cases. We can use a Term Frequency / Inverse document frequency ([TF-IDF](https://en.wikipedia.org/wiki/Tf%E2%80%93idf)) approach to increase weight of user specific locations whilst reducing weight around common areas. We retrieve the number of unique visitor per H3 tile (`df`) and the total number of visits for each user in those same tiles (`tf`). 

$${tfidf}_{i,j} = {tf}_{i,j}\cdot log(\frac{N}{{df}_{i}})$$

In [0]:
points_h3 = points_df.select(F.col('user'), to_h3(F.col('latitude'), F.col('longitude'), F.lit(10)).alias('h3'))
document_frequency = (
  personalized_tiles
    .drop('user')
    .join(points_h3, ['h3'])
    .select('user', 'h3')
    .distinct()
    .groupBy('h3')
    .agg(F.sum(F.lit(1)).alias('df'))
)

In [0]:
term_frequency = (
  personalized_tiles
    .join(points_h3, ['h3', 'user'])
    .groupBy('user', 'h3', 'cluster')
    .agg(F.sum(F.lit(1)).alias('tf'))
)

In [0]:
import math
n = sc.broadcast(document_frequency.count())

@udf('double')
def tf_idf(tf, df):
  return tf * math.log(n.value / df)

personalized_areas = (
  term_frequency
    .join(document_frequency, ['h3'])
    .withColumn('tf_idf', tf_idf(F.col('tf'), F.col('df')))
    .select('user', 'cluster', 'h3', 'tf_idf')
)

display(personalized_areas)

user cluster h3 tf_idf 5a809bee-2483-433f-8e8a-77a9efe43ccf 1 8A2A100D684FFFF 9.471830885747998 5a809bee-2483-433f-8e8a-77a9efe43ccf 0 8A2A100AA377FFF 11.36999199514229 5a809bee-2483-433f-8e8a-77a9efe43ccf 5 8A2A100D3597FFF 4.911806109337663 5a809bee-2483-433f-8e8a-77a9efe43ccf 4 8A2A1072C787FFF 5.972678070022925 5a809bee-2483-433f-8e8a-77a9efe43ccf 4 8A2A1072CAD7FFF 13.496448407049616 5a809bee-2483-433f-8e8a-77a9efe43ccf 4 8A2A100D378FFFF 6.470857428456907 ac1f4c13-c68e-404f-b563-e8a7695ffc1e 1 8A2A10088BA7FFF 210.1405885950646 ac1f4c13-c68e-404f-b563-e8a7695ffc1e 3 8A2A100D662FFFF 4.874065781354816 ac1f4c13-c68e-404f-b563-e8a7695ffc1e 2 8A2A100D3547FFF 27.654226588719432 ac1f4c13-c68e-404f-b563-e8a7695ffc1e 3 8A2A10721957FFF 3.2140755897578845 9fa2a9ef-7b3b-4e43-a9e2-546260276146 2 8A2A10089127FFF 16.59253595323166 9fa2a9ef-7b3b-4e43-a9e2-546260276146 3 8A2A1008B96FFFF 24.959244085056 9fa2a9ef-7b3b-4e43-a9e2-546260276146 5 8A2A10728827FFF 9.902053644981889 9fa2a9ef-7b3b-4e43-a9e2-546260276146 5 8A2A1072C0DFFFF 4.874065781354816 35ce79fc-ac60-41a2-ac24-afb1f5c48b38 4 8A2A100D54D7FFF 10.673378606605858 35ce79fc-ac60-41a2-ac24-afb1f5c48b38 1 8A2A1072D387FFF 5.078860194000829 35ce79fc-ac60-41a2-ac24-afb1f5c48b38 5 8A2A100D2167FFF 5.279530889462981 77268b68-7ff9-4c6e-8e65-af4c6724295f 4 8A2A100D449FFFF 72.8643927686689 77268b68-7ff9-4c6e-8e65-af4c6724295f 2 8A2A100DEC1FFFF 29.863390350114628 77268b68-7ff9-4c6e-8e65-af4c6724295f 2 8A2A100DE19FFFF 23.469270217460398 77268b68-7ff9-4c6e-8e65-af4c6724295f 2 8A2A100DE3B7FFF 16.814859869692825 77268b68-7ff9-4c6e-8e65-af4c6724295f 3 8A2A100D642FFFF 4.704166744559418 41d799fd-eea3-4c5e-8639-23541ec2c7c7 4 8A2A1072C8B7FFF 9.117969469429841 41d799fd-eea3-4c5e-8639-23541ec2c7c7 4 8A2A1072CB87FFF 6.731763205251777 41d799fd-eea3-4c5e-8639-23541ec2c7c7 4 8A2A1072CA1FFFF 12.800357391132579 41d799fd-eea3-4c5e-8639-23541ec2c7c7 3 8A2A1008DB77FFF 6.090461105679309 41d799fd-eea3-4c5e-8639-23541ec2c7c7 4 8A2A1072DCB7FFF 9.907104590710688 41d799fd-eea3-4c5e-8639-23541ec2c7c7 1 8A2A10725AD7FFF 3.2947053241579938 a344b56a-b53a-4205-9dc8-721dd30af7ac 2 8A2A100D3C87FFF 6.514495523246186 3d2b2bb8-15f1-4d77-ac6c-e7ca7f675bab 4 8A2A100D5597FFF 77.64481491029802 3d2b2bb8-15f1-4d77-ac6c-e7ca7f675bab 6 8A2A100D665FFFF 15.522511121415462 04dbe688-0ae6-4f79-b596-8c2a210f0330 1 8A2A100D691FFFF 5.034408431429996 04dbe688-0ae6-4f79-b596-8c2a210f0330 0 8A2A1008B827FFF 14.853080467472832 04dbe688-0ae6-4f79-b596-8c2a210f0330 2 8A2A100D2487FFF 22.547999298866838 04dbe688-0ae6-4f79-b596-8c2a210f0330 2 8A2A100D242FFFF 6.620180485994946 04dbe688-0ae6-4f79-b596-8c2a210f0330 2 8A2A10725B17FFF 5.397313925119364 04dbe688-0ae6-4f79-b596-8c2a210f0330 2 8A2A1072CA27FFF 10.073154875960183 04dbe688-0ae6-4f79-b596-8c2a210f0330 2 8A2A1072CAAFFFF 16.62857780450277 04dbe688-0ae6-4f79-b596-8c2a210f0330 2 8A2A1072180FFFF 13.430873167946912 0c9fef25-e8f2-4a35-bb55-f52a195e8903 3 8A2A107288E7FFF 4.911806109337663 0c9fef25-e8f2-4a35-bb55-f52a195e8903 3 8A2A100D3CA7FFF 3.2646278689207158 950d66d9-8c51-499b-bbcb-33f011714abd 2 8A2A100D6737FFF 191.60919852159924 950d66d9-8c51-499b-bbcb-33f011714abd 0 8A2A100D451FFFF 44.839626319180866 950d66d9-8c51-499b-bbcb-33f011714abd 1 8A2A10721807FFF 14.86222140442255 a96eb275-947c-4d5d-a41d-7030cdc12e2d 3 8A2A1072191FFFF 22.698542735413586 a96eb275-947c-4d5d-a41d-7030cdc12e2d 3 8A2A100D246FFFF 9.902053644981889 a96eb275-947c-4d5d-a41d-7030cdc12e2d 3 8A2A10721A47FFF 14.853080467472832 a96eb275-947c-4d5d-a41d-7030cdc12e2d 3 8A2A1072CA1FFFF 6.400178695566289 70427e5a-49fc-4c16-84d2-df4494d78a7c 2 8A2A1072DC97FFF 3.3257155609005538 70427e5a-49fc-4c16-84d2-df4494d78a7c 1 8A2A100D3C17FFF 3.2140755897578845 636c70a0-2e78-4d9f-ac41-69604a5c2243 2 8A2A1072CB5FFFF 6.6047363938071255 636c70a0-2e78-4d9f-ac41-69604a5c2243 2 8A2A100D3687FFF 3.605554455891309 dfda257a-8520-45a0-be40-06a443fb4e1f 5 8A2A1072C897FFF 18.574168490971935 dfda257a-8520-45a0-be40-06a443fb4e1f 5 8A2A1072CAF7FFF 3.2871007247727744 dfda257a-8520-

By storing all our clusters tiled with H3 polygons, we created a single reference lookup table for any known behavioural pattern. Given a specific user and a H3 location of size 10, we could detect if this location is part of any known and descriptive pattern for that user or if this activity is worth flagging as a unusual behavior. Furthermore, it is worth mentioning that our tiles being stored on Delta lake, it becomes easier to understand previous behaviour and trends using time travel functionality

In [0]:
personalized_areas.write.format('delta').mode('overwrite').saveAsTable('geospatial.tiles')

For faster lookup, we optimize our table for user and H3 access.

In [0]:
%sql
OPTIMIZE geospatial.tiles ZORDER BY (user, h3)

path metrics null List(1, 2, List(426862, 426862, 426862.0, 1, 426862), List(177303, 287407, 232355.0, 2, 464710), 0, List(minCubeSize(107374182400), List(0, 0), List(2, 464710), 0, List(2, 464710), 1, null), 1)

Finally, we can represent the same shapes as earlier for user `823a9ece-c2f1-4175-ad69-6a95ca568f25`, but this time color coded by popularity. Darker is the color, the more descriptive this region is to the specified user.

In [0]:
personalized_tiles = spark.read.table('geospatial.tiles').filter(F.col('user') == user)
display(personalized_tiles)

user cluster h3 tf_idf 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6417FFF 23.679577214369996 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A1072505FFFF 6.5894106483159876 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A100D37AFFFF 3.3658816026258886 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 4 8A2A100888D7FFF 177.66576471855197 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2677FFF 48.57582532607427 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6477FFF 4.735915442873999 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D2D6FFFF 10.559061778925962 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D665FFFF 15.522511121415462 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6597FFF 27.68732751521839 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D62B7FFF 4.911806109337663 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072CAA7FFF 10.097644807877666 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A1008B247FFF 18.816666978237674 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 1 8A2A100D3D97FFF 9.749765164593061 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072C8CFFFF 3.2795535191373917 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072DC17FFF 9.70628614268536 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072DD67FFF 3.2354287142284535 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072DCF7FFF 6.559107038274783 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 3 8A2A10089227FFF 67.264214859467 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D2D67FFF 15.676391004578115 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D25A7FFF 13.33448296163067 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072DD6FFFF 3.2646278689207158 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A1072530FFFF 10.848077267275812 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D645FFFF 18.574168490971935 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 1 8A2A100D231FFFF 18.574168490971935 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 1 8A2A100D2A97FFF 18.943661771495997 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 3 8A2A1008926FFFF 88.49352508390218 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 3 8A2A100D45A7FFF 110.61690635487773 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 4 8A2A100888AFFFF 224.69493773228632 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072DCA7FFF 12.999686886124081 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A107252DFFFF 6.5292557378414315 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A1072594FFFF 9.287084245485968 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2317FFF 5.684995997571145 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 0 8A2A100F2207FFF 27.309262231284674 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 2 8A2A1072CAEFFFF 6.4852979244038815 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6487FFF 9.34679017178533 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D659FFFF 32.10468596232125 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D608FFFF 13.759151126709106 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A1072191FFFF 6.4852979244038815 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A10725327FFF 3.3023681969035628 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A10725B77FFF 15.676391004578115 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A10725817FFF 9.537410531393979 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A1072195FFFF 3.2947053241579938 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 1 8A2A100D2377FFF 13.271489533758112 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A107250E7FFF 7.78647305668618 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 1 8A2A100D23AFFFF 42.33750070103476 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 4 8A2A100888DFFFF 47.029173013734344 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6537FFF 14.020185257677994 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 4 8A2A1008D5A7FFF 5.461852446256935 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D2987FFF 44.64700224691763 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6697FFF 19.074821062787958 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D29AFFFF 25.172042157149978 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A10725A77FFF 30.206450588579976 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 3 8A2A10089257FFF 15.838592668388943 8d08c2ba-6e15-4bb0-aa6c-d4d319ed2d6d 5 8A2A100D6717FFF 18.235938938859682 8d08c

In [0]:
personalized_density = personalized_tiles.groupBy('cluster').agg(F.max('tf_idf').alias('max_tf_idf')).toPandas()[['cluster', 'max_tf_idf']]
personalized_geojson = geoJsons.filter(F.col('user') == user).toPandas().cluster.iloc[0]
data_bins = list(personalized_density.max_tf_idf.quantile([0, 0.25, 0.5, 0.6, 0.7, 0.8, 0.9, 1]))
nyc_personalized = folium.Map([40.75466940037548,-73.98365020751953], zoom_start=12, width='80%', height='100%')
folium.TileLayer('Stamen Toner').add_to(nyc_personalized)

# Color least popular areas by quantile
folium.Choropleth(
    geo_data = personalized_geojson,
    name='choropleth',
    data = personalized_density,
    columns=['cluster','max_tf_idf'],
    key_on='feature.id',
    fill_color='BuPu',
    fill_opacity=0.9,
    line_opacity=0.7,
    bins = data_bins
).add_to(nyc_personalized)

nyc_personalized

Out[29]:

Make this Notebook Trusted to load map: File -> Trust Notebook <iframe src="about:blank" style="position:absolute;width:100%;height:100%;left:0;top:0;border:none !important;" data-html=%3C%21DOCTYPE%20html%3E%0A%3Chead%3E%20%20%20%20%0A%20%20%20%20%3Cmeta%20http-equiv%3D%22content-type%22%20content%3D%22text/html%3B%20charset%3DUTF-8%22%20/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%3Cscript%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20L_NO_TOUCH%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20L_DISABLE_3D%20%3D%20false%3B%0A%20%20%20%20%20%20%20%20%3C/script%3E%0A%20%20%20%20%0A%20%20%20%20%3Cstyle%3Ehtml%2C%20body%20%7Bwidth%3A%20100%25%3Bheight%3A%20100%25%3Bmargin%3A%200%3Bpadding%3A%200%3B%7D%3C/style%3E%0A%20%20%20%20%3Cstyle%3E%23map%20%7Bposition%3Aabsolute%3Btop%3A0%3Bbottom%3A0%3Bright%3A0%3Bleft%3A0%3B%7D%3C/style%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//code.jquery.com/jquery-1.12.4.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/js/bootstrap.min.js%22%3E%3C/script%3E%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.js%22%3E%3C/script%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/npm/leaflet%401.6.0/dist/leaflet.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/bootstrap/3.2.0/css/bootstrap-theme.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//maxcdn.bootstrapcdn.com/font-awesome/4.6.3/css/font-awesome.min.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/Leaflet.awesome-markers/2.0.2/leaflet.awesome-markers.css%22/%3E%0A%20%20%20%20%3Clink%20rel%3D%22stylesheet%22%20href%3D%22https%3A//cdn.jsdelivr.net/gh/python-visualization/folium/folium/templates/leaflet.awesome.rotate.min.css%22/%3E%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cmeta%20name%3D%22viewport%22%20content%3D%22width%3Ddevice-width%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20initial-scale%3D1.0%2C%20maximum-scale%3D1.0%2C%20user-scalable%3Dno%22%20/%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cstyle%3E%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%23map_104d6a0b3ebd4295a060233613308c51%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20position%3A%20relative%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20width%3A%2080.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20height%3A%20100.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20left%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20top%3A%200.0%25%3B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7D%0A%20%20%20%20%20%20%20%20%20%20%20%20%3C/style%3E%0A%20%20%20%20%20%20%20%20%0A%20%20%20%20%3Cscript%20src%3D%22https%3A//cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min.js%22%3E%3C/script%3E%0A%3C/head%3E%0A%3Cbody%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20%3Cdiv%20class%3D%22folium-map%22%20id%3D%22map_104d6a0b3ebd4295a060233613308c51%22%20%3E%3C/div%3E%0A%20%20%20%20%20%20%20%20%0A%3C/body%3E%0A%3Cscript%3E%20%20%20%20%0A%20%20%20%20%0A%20%20%20%20%20%20%20%20%20%20%20%20var%20map_104d6a0b3ebd4295a060233613308c51%20%3D%20L.map%28%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%22map_104d6a0b3ebd4295a060233613308c51%22%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%7B%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20center%3A%20%5B40.75466940037548%2C%20-73.98365020751953%5D%2C%0A%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%20%

We suddely have gained incredible insights about our customer's shopping behaviour. Although the core of their transactions are made in the chelsea and the financial district area, what seems to better define this user are his / her transactions around the Plaza Hotel and Williamsburg. @Junta??

## Paving the way to fraud detection
In this notebook, we have introduced a novel approach geospatial clustering in order to gain further insights on user shopping behaviour. We showed how to leverage the information from our entire customer base to better understand users' specific behaviours from large regions down to a few meters and demonstrated the importance to track customer changes over time using Delta as our underlying customer 360 strategy. Although we used a synthetic dataset, we showed that geospatial analysis can tell us a lot of information about customers behaviour, hence a critical component to anomaly detection and fraud prevention. In the next [notebook](https://databricks.com/notebooks/geoscan/02_geofraud_fraud.html), we will demonstrate how to use our "tiling" approach to detect suspicious behaviour in real time outside of a spark environment with high SLA and low latency requirements

---
+ <a href="https://databricks.com/notebooks/geoscan/00_geofraud_context.html">STAGE0</a>: Home page
+ <a href="https://databricks.com/notebooks/geoscan/01_geofraud_clustering.html">STAGE1</a>: Using a novel approach to geospatial clustering with H3
+ <a href="https://databricks.com/notebooks/geoscan/02_geofraud_fraud.html">STAGE2</a>: Detecting anomalous transactions as ML enriched rules
---

&copy; 2021 Databricks, Inc. All rights reserved. The source in this notebook is provided subject to the Databricks License [https://databricks.com/db-license-source].  All included or referenced third party libraries are subject to the licenses set forth below.

| library                                | description             | license    | source                                              |
|----------------------------------------|-------------------------|------------|-----------------------------------------------------|
| com.uber:h3:3.6.3                      | Uber geospatial library | Apache2    | https://github.com/uber/h3                          |
| h3                                     | Uber geospatial library | Apache2    | https://github.com/uber/h3-py                       |
| org.scala-graph:graph-core_2.12:1.12.5 | Scala graph             | Apache2    | https://github.com/scala-graph/scala-graph          |
| com.databricks.labs:geoscan:0.0.1      | Geoscan algorithm       | Databricks | https://github.com/databrickslabs/geoscan           |
| folium                                 | Geospatial visualization| MIT        | https://github.com/python-visualization/folium      |
| pybloomfiltermmap3                     | Bloom filter            | MIT        | https://github.com/prashnts/pybloomfiltermmap3      |